Our task is to design an IR system on the given dataset which can be found [here](https://drive.google.com/drive/folders/1h7AzOoPrbaEx2ApcGq-MO22quMcOi40H?usp=share_link. "link to dataset").

# STEP 1: dataset input
reading the files from the dataset. In order to do this we use pandas to read the xml data as input. However since the provided xml file lacks a root, we add the root ourself.

In [91]:
# importing element tree
import pandas as pd

df = pd.read_xml("cran.all.1400.xml")

print(df.info())

file_names = []
temp = df.loc[:,"title"]
for value in temp:
    if value is not None:
        file_names.append(value)

#file_names = [file_names[0]]
print(file_names)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1400 entries, 0 to 1399
Data columns (total 5 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   docno   1400 non-null   int64 
 1   title   1398 non-null   object
 2   author  1347 non-null   object
 3   bib     1330 non-null   object
 4   text    1398 non-null   object
dtypes: int64(1), object(4)
memory usage: 54.8+ KB
None
['experimental investigation of the aerodynamics of a\nwing in a slipstream .', 'simple shear flow past a flat plate in an incompressible fluid of small\nviscosity .', 'the boundary layer in simple shear flow past a flat plate .', 'approximate solutions of the incompressible laminar\nboundary layer equations for a plate in shear flow .', 'one-dimensional transient heat conduction into a double-layer\nslab subjected to a linear heat input for a small time\ninternal .', 'one-dimensional transient heat flow in a multilayer\nslab .', 'the effect of controlled three-dimensional roughn

Now that we have all the names, we can start by reading the content of every file:

In [92]:
#list of document content
file_content = []

temp = df.loc[:,"text"]
for value in temp:
    if value is not None:
        file_content.append(value)

#file_content = [file_content[0]]
print(file_content)

['experimental investigation of the aerodynamics of a\nwing in a slipstream .\n  an experimental study of a wing in a propeller slipstream was\nmade in order to determine the spanwise distribution of the lift\nincrease due to slipstream at different angles of attack of the wing\nand at different free stream to slipstream velocity ratios .  the\nresults were intended in part as an evaluation basis for different\ntheoretical treatments of this problem .\n  the comparative span loading curves, together with\nsupporting evidence, showed that a substantial part of the lift increment\nproduced by the slipstream was due to a /destalling/ or\nboundary-layer-control effect .  the integrated remaining lift\nincrement, after subtracting this destalling lift, was found to agree\nwell with a potential flow theory .\n  an empirical evaluation of the destalling effects was made for\nthe specific configuration of the experiment .', "simple shear flow past a flat plate in an incompressible fluid of sma

# STEP 2: tokenizing
Now that we have the text in our program we should start by tokenizing the text.
In order to do this we're going to use the nltk library in python and to make our job easier we're going to tokenize words separated by Space, Comma, and dash.

Examples:
1. I live ...
2. Student, jason, ...
3. 30-year-old

In [93]:
from nltk.tokenize import RegexpTokenizer

# A list for tokenized texts
file_content_tokenized = []

# Define a regular expression pattern to match words separated by Space, Comma, and Dash
#pattern = r'\w+|\$[\d\.]+'
pattern = r'\d{1,4}(?:,\d{3})*(?:\.\d+)?|\w+'
#pattern = r'[A-Za-z0-9]+.*[A-Za-z0-9]+.*([+-]?(?=\.\d|\d)(?:\d+)?(?:\.?\d*))(?:[Ee]([+-]?\d+))?.*([0-9]+(,[0-9]+)+)'

#Change all input data into tokens
for file in file_content:
    # Use regex_tokenize with the defined pattern
    file_content_tokenized.append(RegexpTokenizer(pattern).tokenize(file))
    print(file_content_tokenized[-1])


['experimental', 'investigation', 'of', 'the', 'aerodynamics', 'of', 'a', 'wing', 'in', 'a', 'slipstream', 'an', 'experimental', 'study', 'of', 'a', 'wing', 'in', 'a', 'propeller', 'slipstream', 'was', 'made', 'in', 'order', 'to', 'determine', 'the', 'spanwise', 'distribution', 'of', 'the', 'lift', 'increase', 'due', 'to', 'slipstream', 'at', 'different', 'angles', 'of', 'attack', 'of', 'the', 'wing', 'and', 'at', 'different', 'free', 'stream', 'to', 'slipstream', 'velocity', 'ratios', 'the', 'results', 'were', 'intended', 'in', 'part', 'as', 'an', 'evaluation', 'basis', 'for', 'different', 'theoretical', 'treatments', 'of', 'this', 'problem', 'the', 'comparative', 'span', 'loading', 'curves', 'together', 'with', 'supporting', 'evidence', 'showed', 'that', 'a', 'substantial', 'part', 'of', 'the', 'lift', 'increment', 'produced', 'by', 'the', 'slipstream', 'was', 'due', 'to', 'a', 'destalling', 'or', 'boundary', 'layer', 'control', 'effect', 'the', 'integrated', 'remaining', 'lift', 'in

# STEP 3: lowercasing
We now want to lowercase our tokens:

In [94]:
#lowercasing each token individually
for i in range(len(file_content_tokenized)):
    for j in range(len(file_content_tokenized[i])):
        file_content_tokenized[i][j] = file_content_tokenized[i][j].lower()
    print(file_content_tokenized[i])


['experimental', 'investigation', 'of', 'the', 'aerodynamics', 'of', 'a', 'wing', 'in', 'a', 'slipstream', 'an', 'experimental', 'study', 'of', 'a', 'wing', 'in', 'a', 'propeller', 'slipstream', 'was', 'made', 'in', 'order', 'to', 'determine', 'the', 'spanwise', 'distribution', 'of', 'the', 'lift', 'increase', 'due', 'to', 'slipstream', 'at', 'different', 'angles', 'of', 'attack', 'of', 'the', 'wing', 'and', 'at', 'different', 'free', 'stream', 'to', 'slipstream', 'velocity', 'ratios', 'the', 'results', 'were', 'intended', 'in', 'part', 'as', 'an', 'evaluation', 'basis', 'for', 'different', 'theoretical', 'treatments', 'of', 'this', 'problem', 'the', 'comparative', 'span', 'loading', 'curves', 'together', 'with', 'supporting', 'evidence', 'showed', 'that', 'a', 'substantial', 'part', 'of', 'the', 'lift', 'increment', 'produced', 'by', 'the', 'slipstream', 'was', 'due', 'to', 'a', 'destalling', 'or', 'boundary', 'layer', 'control', 'effect', 'the', 'integrated', 'remaining', 'lift', 'in

# STEP 4: stopword removal
Now we want to remove the stopwords present in our text. To do this task we use the library of stopwords in nltk library. Please note that in order to be able to perform positional queries, we will not delete stopwords, just replace them with empty strings.

In [95]:
from nltk.corpus import stopwords

#Setting the stopword language
stop_words = set(stopwords.words("english"))
print(stop_words)

for i in range(len(file_content_tokenized)):
    j = 0
    #print(file_content_tokenized[i])
    while j < len(file_content_tokenized[i]):
        if file_content_tokenized[i][j] in stop_words:
            #print("got here with ", file_content_tokenized[i][j])
            #file_content_tokenized[i] = file_content_tokenized[i][:j]+file_content_tokenized[i][j+1:]
            file_content_tokenized[i] = file_content_tokenized[i][:j] + file_content_tokenized[i][j+1:]
        else:
            j += 1
    print(file_content_tokenized[i])



{'we', 'until', 'its', 'hasn', 'have', 'no', "it's", 'down', 'in', 'at', 'myself', 'mightn', 'below', 'from', 'any', 'once', 'about', "mustn't", 'should', 'being', 'were', 're', 'd', "shouldn't", "you'd", 'was', 'with', 'further', 'you', 'theirs', 'are', 'wouldn', 'themselves', 'too', "you'll", 'by', 'an', 'she', 'against', 'won', 'doesn', 'nor', 'my', 'weren', 'or', 'through', 'yourselves', 've', "mightn't", "wasn't", 'while', 'isn', 'own', "haven't", "needn't", 'll', 'do', 'there', 'having', 'which', 'to', 'than', 'up', 'over', "doesn't", "you're", 'above', 'haven', 'hers', 'the', 'don', 'each', 'wasn', "weren't", "didn't", 'your', 'his', "don't", 'needn', 'same', 'had', "couldn't", 'why', 'not', 'yours', 'doing', 'ain', 'those', 'most', 'has', 'on', 'm', 'here', 'and', 'herself', 'where', 'her', 'other', 'some', "should've", 'himself', 'only', 'for', 'ourselves', "she's", 'their', 'them', 'now', 'will', 'because', 'off', 'couldn', 'how', "hadn't", 'whom', 'between', 'didn', 'ma', 'o

# STEP 5: stemming
Now that we have tokenized, lowercased, and removed stopwords, we are going to stem the words to optimize our IR system.

In [59]:
from nltk.stem import PorterStemmer

# Initializing the Porter Stemmer
stemmer = PorterStemmer()

#Stemming each token individually
for i in range(len(file_content_tokenized)):
    for j in range(len(file_content_tokenized[i])):
        file_content_tokenized[i][j] = PorterStemmer().stem(file_content_tokenized[i][j])
    print(file_content_tokenized[i])


['experi', 'investig', 'aerodynam', 'wing', 'slipstream', 'experi', 'studi', 'wing', 'propel', 'slipstream', 'made', 'order', 'determin', 'spanwi', 'distribut', 'lift', 'increa', 'due', 'slipstream', 'differ', 'angl', 'attack', 'wing', 'differ', 'free', 'stream', 'slipstream', 'veloc', 'ratio', 'result', 'intend', 'part', 'evalu', 'basi', 'differ', 'theoret', 'treatment', 'problem', 'compar', 'span', 'load', 'curv', 'togeth', 'support', 'evid', 'show', 'substanti', 'part', 'lift', 'increment', 'produc', 'slipstream', 'due', 'destal', 'boundari', 'layer', 'control', 'effect', 'integr', 'remain', 'lift', 'increment', 'subtract', 'destal', 'lift', 'found', 'agr', 'well', 'potenti', 'flow', 'theori', 'empir', 'evalu', 'destal', 'effect', 'made', 'specif', 'configur', 'experi']
['simpl', 'shear', 'flow', 'past', 'flat', 'plate', 'incompress', 'fluid', 'small', 'visco', 'studi', 'high', 'speed', 'viscou', 'flow', 'past', 'two', 'dimen', 'bodi', 'usual', 'necessari', 'consid', 'curv', 'shock'

# STEP 6: inverted index
Now that we have done all the preprocessing, we want to create our Inverted Index.

In [96]:
from collections import defaultdict

# Initialize the DF array
#document_frequency = defaultdict(int)

# Initialize the inverted index
inverted_index = defaultdict(list)

# Build the inverted index
for doc_id in range(len(file_content_tokenized)):
    for token_id in range(len(file_content_tokenized[doc_id])):
        if file_content_tokenized[doc_id][token_id] == "":
            continue
        #if inverted_index[file_content_tokenized[doc_id][token_id]][-1] != doc_id:
        inverted_index[file_content_tokenized[doc_id][token_id]].append((doc_id))
        
        #if document_frequency[file_content_tokenized[doc_id][token_id]] == None:
        #    document_frequency[file_content_tokenized[doc_id][token_id]] = 0
        #document_frequency[file_content_tokenized[doc_id][token_id]] += 1

#Print the inverted index
for term, doc_ids in inverted_index.items():
    print(f"Term: {term}, Document IDs: {doc_ids}")
    #print(document_frequency[term])


print(len(inverted_index))

dictionary = set()
#Building the dictionary for spellchecking
for doc_id in range(len(file_content_tokenized)):
    for token_id in range(len(file_content_tokenized[doc_id])):
        if file_content_tokenized[doc_id][token_id] != "" and not (True in [(str(num) in file_content_tokenized[doc_id][token_id]) for num in range(10)]):
            dictionary.add(file_content_tokenized[doc_id][token_id])
print("dictionary = ", dictionary)
print(len(dictionary))

Term: experimental, Document IDs: [0, 0, 10, 11, 16, 18, 24, 28, 29, 34, 40, 41, 46, 51, 52, 57, 68, 69, 73, 77, 83, 83, 98, 98, 100, 102, 111, 114, 120, 122, 122, 136, 139, 141, 153, 155, 167, 169, 170, 172, 172, 175, 178, 178, 182, 183, 185, 185, 186, 187, 188, 190, 194, 194, 194, 196, 196, 201, 202, 205, 205, 206, 206, 211, 215, 219, 221, 224, 226, 229, 233, 233, 233, 233, 244, 250, 255, 255, 256, 261, 270, 270, 272, 276, 281, 282, 285, 293, 294, 303, 306, 328, 328, 329, 333, 333, 337, 338, 343, 343, 344, 345, 345, 346, 353, 359, 368, 369, 371, 371, 376, 396, 408, 410, 410, 412, 412, 417, 419, 420, 422, 426, 434, 438, 440, 441, 441, 452, 454, 454, 461, 463, 466, 482, 482, 482, 492, 492, 494, 495, 496, 499, 501, 502, 503, 509, 516, 518, 518, 520, 520, 520, 534, 538, 542, 542, 547, 550, 550, 551, 556, 561, 565, 567, 570, 570, 570, 570, 574, 586, 593, 598, 604, 608, 630, 632, 633, 634, 642, 643, 647, 660, 661, 661, 664, 664, 668, 673, 676, 677, 683, 683, 683, 686, 686, 686, 687, 687, 6

STEP 6.5: PARAMETER SETTING
We now set the query and K parameter for the search:

In [123]:
query = "what are the structural and aeroelastic problems associated with flight of high speed aircraft ."
k = 25

# TOKENIZATION
pattern = r'\d{1,4}(?:,\d{3})*(?:\.\d+)?|\w+'
query = RegexpTokenizer(pattern).tokenize(query)

# LOWER CASING
for i in range(len(query)):
    query[i] = query[i].lower()

# STOP WORD REMOVAL
i = 0
while i < len(query):
    if query[i] in stop_words:
        query = query[:i]+query[i+1:]
    else:
        i += 1

#for i in range(len(query)):
#    query[i] = PorterStemmer().stem(query[i])

print(query)

['structural', 'aeroelastic', 'problems', 'associated', 'flight', 'high', 'speed', 'aircraft']


# STEP 7: TF-IDF
We define the TF and IDF function as described in the slides

In [124]:
import math

def calculate_tf(document):
    """calculates the tf

    Args:
        document (list): single document

    Returns:
        dict: tf
    """
    term_frequency = {}
    total_terms = len(document)

    for term in document:
        term_frequency[term] = term_frequency.get(term, 0) + 1

    tf = {term: freq / total_terms for term, freq in term_frequency.items()}
    return tf

def calculate_idf(documents):
    """calculates the idf

    Args:
        documents (list): corpus.

    Returns:
        dict: idf.
    """
    total_documents = len(documents)
    term_document_count = {}

    for document in documents:
        unique_terms = set(document)
        for term in unique_terms:
            term_document_count[term] = term_document_count.get(term, 0) + 1

    idf = {term: math.log(total_documents / (count + 1)) for term, count in term_document_count.items()}
    return idf

def calculate_tfidf_matrix(documents):
    """given a corpus calculates the tfidf matrics

    Args:
        documents (list): corpus.

    Returns:
        list: tf-idf.
    """
    tf_matrix = [calculate_tf(doc) for doc in documents]
    idf_matrix = calculate_idf(documents)

    terms = list(idf_matrix.keys())
    tfidf_matrix = np.zeros((len(documents), len(terms)))

    for i, tf in enumerate(tf_matrix):
        for j, term in enumerate(terms):
            tfidf_matrix[i, j] = tf.get(term, 0) * idf_matrix[term]

    return tfidf_matrix, terms



# STEP 8: COSINE
We implement the cosine similarity using the definition of tf and idf with the help of sklearn library

In [125]:
import numpy as np

def calculate_cosine_similarity(query_vector, document_vectors):
    """The Cosine similarity calculated by using dot product from numpy

    Args:
        query_vector (list): query vector.
        document_vectors (list): particular document vector.

    Returns:
        list: the similarity vector.
    """
    similarities = np.dot(document_vectors, query_vector) / (np.linalg.norm(document_vectors, axis=1) * np.linalg.norm(query_vector))
    return similarities


# STEP 9: TF-IDF QUERY
We now use the Tf-Idf to retrieve queries

In [126]:
# Calculate TF-IDF matrix
tfidf_matrix, terms = calculate_tfidf_matrix(file_content_tokenized + [query])

# Print TF-IDF matrix
print("TF-IDF Matrix:")
print(tfidf_matrix)

# Extract query vector and document vectors
query_vector = tfidf_matrix[-1, :]
document_vectors = tfidf_matrix[:-1, :]

# Calculate cosine similarity
similarities = calculate_cosine_similarity(query_vector, document_vectors)

# Retrieve top-K documents
top_k_indices = similarities.argsort()[:-k-1:-1]
top_k_documents = [file_content_tokenized[i] for i in top_k_indices]

# Print results
print("\nCosine Similarity with Query:")
print(similarities)

print(f"\nTop {k} Documents:")
for i, doc in enumerate(top_k_documents):
    #print(f"Rank {similarities[top_k_indices[i]]}: {top_k_indices[i]} which {doc}")
    print(top_k_indices[i])

TF-IDF Matrix:
[[0.03865643 0.05146151 0.0348619  ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 ...
 [0.         0.         0.         ... 0.         0.12843854 0.        ]
 [0.         0.         0.         ... 0.         0.         0.10397406]
 [0.         0.         0.         ... 0.         0.         0.        ]]

Cosine Similarity with Query:
[0.         0.02278943 0.         ... 0.         0.         0.        ]

Top 25 Documents:
11
50
744
882
1166
183
13
873
1039
140
790
724
252
577
1167
881
99
428
722
1260
808
831
604
779
1160


# STEP 9: OKAPI BM25
Implementing the Okapi BM25 using the implementation provided in the lecture 9

In [132]:
#from collections import Counter

def bm25(document, query, document_lengths, average_document_length, document_frequencies, total_documents, k1=1.5, b=0.75):
    """calculates the BM25 score of a query and a document length

    Args:
        document (list): a list of words.
        query (list): a list of words.
        document_lengths (int): lengths of the documents
        average_document_length (float): average length of the documents
        document_frequencies (int): DF values
        total_documents (int): total corpus size of this instance of Okapi BM25
        k1 (float, optional): the k1 value of the Okapi. Defaults to 1.5.
        b (float, optional): the b value of the okapu. Defaults to 0.75.

    Returns:
        _type_: _description_
    """
    score = 0.0
    for term in set(query):
        f_q_d = document.count(term)
        n_q = document_frequencies.get(term, 0)
        dl = document_lengths
        avgdl = average_document_length

        idf_term = math.log((total_documents - n_q + 0.5) / (n_q + 0.5) + 1.0)
        numerator = f_q_d * (k1 + 1.0)
        denominator = f_q_d + k1 * (1.0 - b + b * (dl / avgdl))

        score += idf_term * numerator / denominator

    return score

def calculate_average_document_length():
    """calculates documents average length.

    Returns:
        float: document average length.
    """
    total_terms = sum(len(doc) for doc in file_content_tokenized)
    total_documents = len(file_content_tokenized)
    return total_terms / total_documents

def calculate_document_frequencies():
    """calculates DFs in the corpus.

    Returns:
        dict: DF.
    """
    term_document_frequencies = {}
    for document in file_content_tokenized:
        unique_terms = set(document)
        for term in unique_terms:
            term_document_frequencies[term] = term_document_frequencies.get(term, 0) + 1
    return term_document_frequencies


# STEP 10: OKAPI BM25 QUERY
Used the implemented okapi model above to calculated the top k documents given a query.

In [133]:
# Calculate average document length and document frequencies
avg_document_length = calculate_average_document_length()
document_frequencies = calculate_document_frequencies()

# Calculate BM25 scores for each document
bm25_scores = [bm25(doc, query, len(doc), avg_document_length, document_frequencies, len(file_content_tokenized)) for doc in file_content_tokenized]

# Retrieve Top-K Documents
top_k_indices = sorted(range(len(bm25_scores)), key=lambda i: bm25_scores[i], reverse=True)[:k]
top_k_documents = [file_content_tokenized[i] for i in top_k_indices]

# Print results
print("BM25 Scores:")
print(bm25_scores)

print(f"\nTop {k} Documents:")
for i, doc in enumerate(top_k_documents):
    #print(f"Rank {bm25_scores[top_k_indices[i]]}: {top_k_indices[i]} which {doc}")
    print(top_k_indices[i])

BM25 Scores:
[0.0, 3.478837625671333, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.369770019416434, 0.0, 3.6374407883499886, 31.882285051447763, 0.0, 14.63172907235911, 0.0, 3.2888512382747828, 0.0, 0.0, 2.7799884075077514, 0.0, 0.0, 0.0, 0.0, 4.940612540610542, 2.332665136281015, 0.0, 0.0, 2.3744775440240966, 6.087021765220134, 0.0, 0.0, 2.0339843409219944, 6.921166461734474, 1.6474494676115308, 0.0, 6.70319364393369, 2.3135804298084577, 4.896518736005039, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 4.89763123085746, 8.709079544156204, 0.0, 1.4394081610887628, 0.0, 15.056925524183207, 5.772657047559027, 0.0, 0.0, 0.0, 0.0, 0.0, 6.479631179333145, 0.0, 2.327784305467824, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.050100487318703, 0.0, 5.509877585959079, 4.442976821775101, 0.0, 0.0, 1.5974333123243902, 0.0, 7.907447114846134, 5.687005458403937, 4.195019112549815, 9.73817094703771, 1.7077926110505597, 0.0, 0.0, 6.832223673149182, 2.0143348267082986, 0.0, 4.102043008881033, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 8.765966289915715

# STEP 11: LANGUAGE MODEL
Implemented the language mdoel as stated in lecture 10 and 13

In [129]:
def query_likelihood_model(document, query, smoothing_parameter=0.1):
    """Compute the probability of a query given a document using the Query Likelihood Model.

    Args:
        document (list): A list of words representing the document.
        query (list): A list of words representing the query.
        smoothing_parameter (float, optional): Smoothing parameter to handle unseen terms.

    Returns:
        float: Probability of the query given the document.
    """
    document_length = len(document)
    query_length = len(query)
    document_word_counts = Counter(document)

    probability = 1.0

    for term in query:
        term_frequency = document_word_counts.get(term, 0)
        term_probability = (term_frequency + smoothing_parameter) / (document_length + smoothing_parameter * (len(set(document)) + 1))
        probability *= term_probability

    return probability

def rank_documents(query):
    """Rank documents based on the Query Likelihood Model.

    Args:
        query (list): A list of words representing the query.

    Returns:
        list: A list of documents ranked in descending order of probability.
    """
    rankings = [(i, query_likelihood_model(doc, query)) for i, doc in enumerate(file_content_tokenized)]
    rankings.sort(key=lambda x: x[1], reverse=True)
    ranked_documents = [file_content_tokenized[i] for i, _ in rankings]
    return (ranked_documents, rankings)


In [131]:
# Rank documents using the Query Likelihood Model
ranked_documents = rank_documents(query)

# Print results
print(f"Top {k} Documents:")
for i in range(k):
    #print(f"Rank {ranked_documents[1][i][1]}: {ranked_documents[1][i][0]} which {ranked_documents[0][i]}")
    print(ranked_documents[1][i][0])


Top 25 Documents:
11
428
744
605
500
873
284
1042
1039
319
505
140
1086
576
2
237
222
882
1108
404
668
698
876
1155
852
